<a href="https://colab.research.google.com/github/wiatrak2/BScThesis/blob/master/visualization_in_class_predictor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')
import sys
sys.path.append('BScThesis/')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [2]:
!pip3 install torch torchvision

    100% |████████████████████████████████| 591.8MB 30kB/s 
tcmalloc: large alloc 1073750016 bytes == 0x627f0000 @  0x7ffbf42452a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641
    100% |████████████████████████████████| 61kB 22.6MB/s 
    100% |████████████████████████████████| 2.0MB 3.9MB/s 
  Found existing installation: Pillow 4.0.0
    Uninstalling Pillow-4.0.0:
      Successfully uninstalled Pillow-4.0.0


In [4]:
!git clone https://github.com/wiatrak2/BScThesis

Cloning into 'BScThesis'...
remote: Enumerating objects: 159, done.
remote: Counting objects: 100% (159/159), done.
remote: Compressing objects: 100% (133/133), done.
remote: Total 338 (delta 89), reused 66 (delta 26), pack-reused 179
Receiving objects: 100% (338/338), 49.35 MiB | 4.66 MiB/s, done.
Resolving deltas: 100% (188/188), done.


In [0]:
from importlib import reload 

In [0]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

In [0]:
import torchvision
import torchvision.transforms as transforms

In [0]:
import matplotlib.pyplot as plt
import pickle
import sympy
from collections import defaultdict, namedtuple
import copy

In [0]:
from mnist_m import Mnist_M
from random_dataset import RandomDataset
import datasets_merge
import models
import svhn_models
import trainer
import domain_trainer
from test_model import test_model
import plots
import test
import plotly_plots

In [0]:
import plotly
from plotly import tools
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go

In [0]:
def convertMnist(img):
  img = img.squeeze().numpy()
  return torch.from_numpy(np.tile(img, (3,1,1)))

In [0]:
batch_size=128
num_workers=1

In [13]:
mnist_transform=transforms.Compose([
                           transforms.ToTensor(),
                           transforms.Normalize((0.1307, 0.1307, 0.1307), (0.3081, 0.3081, 0.3081)),
                           transforms.Lambda(convertMnist)
                       ])

mnist_train_set = torchvision.datasets.MNIST(root='./data', train=True, download=True,
                                     transform=mnist_transform)
mnist_train_loader = torch.utils.data.DataLoader(mnist_train_set, batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)

mnist_test_set = torchvision.datasets.MNIST(root='./data', train=False, download=True,
                                     transform=mnist_transform)
mnist_test_loader = torch.utils.data.DataLoader(mnist_test_set, batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)





Processing...
Done!


In [0]:
mnist_m_transform = transforms.Compose([
                           transforms.Normalize((0.1307, 0.1307, 0.1307), (0.3081, 0.3081, 0.3081)),
                       ])
mnist_m_train_set = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',
                        transform=mnist_m_transform)
mnist_m_test_set = Mnist_M('drive/My Drive/BScThesis/keras_mnistm.pkl',train=False,
                     transform=mnist_m_transform)
mnist_m_train_loader = torch.utils.data.DataLoader(mnist_m_train_set, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
mnist_m_test_loader = torch.utils.data.DataLoader(mnist_m_test_set,
                                                  batch_size=batch_size,
                                         shuffle=False, num_workers=num_workers)

In [0]:
merge_train_set = datasets_merge.Merge_Datasets([mnist_train_set, mnist_m_train_set], get_labels=False)
merge_test_set = datasets_merge.Merge_Datasets([mnist_test_set, mnist_m_test_set], get_labels=False)
merge_train_loader = torch.utils.data.DataLoader(merge_train_set, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)
merge_test_loader = torch.utils.data.DataLoader(merge_test_set, 
                                                   batch_size=batch_size,
                                         shuffle=True, num_workers=num_workers)

In [0]:
log_interval = 100

In [0]:
use_cuda = True
use_cuda = use_cuda and torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

In [0]:
lr = 0.01
momentum=0.9

In [0]:
Models = namedtuple('Models', ['model_f', 'model_c', 'model_d'])
Optims = namedtuple('Optims', ['optim_f', 'optim_c', 'optim_d'])
Criterions = namedtuple('Criterions', ['criterion', 'criterion_domain'])
Loaders = namedtuple('Loaders', ['train_loader', 'train_loader_domain',
                                'source_test_loader', 'target_test_loader',
                                'merged_test_loader'])

In [0]:
loaders = Loaders(mnist_train_loader, mnist_m_train_loader,
                 mnist_test_loader, mnist_m_test_loader, merge_test_loader)

In [0]:
criterion = F.nll_loss
criterion_domain = F.nll_loss

In [0]:
criterions = Criterions(criterion, criterion_domain)

In [0]:
epochs=10

In [0]:
model_f = models.MnistFeatureExtractor().to(device)
model_c = models.MnistClassifier3D().to(device)
model_d = models.MnistDomain().to(device)

In [0]:
optim_f = optim.SGD(model_f.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_c = optim.SGD(model_c.parameters(), lr=lr, momentum=momentum, nesterov=True)
optim_d = optim.SGD(model_d.parameters(), lr=lr, momentum=momentum, nesterov=True)

In [0]:
train_models = Models(model_f, model_c, model_d)
optims = Optims(optim_f, optim_c, optim_d)

In [0]:
model_trainer = trainer.Trainer(train_models, optims, criterions, device,
                                train_domain=True, tune_lr=True)

In [0]:
test_history = defaultdict(lambda:[])
model_trainer.train(epochs, loaders, test_history=test_history)

Train Epoch: 					1 [0/60000 (0%)]	Loss: 2.341626, lr: 0.01000 lambd: 0.00000
Train Epoch: 					1 [12800/60000 (21%)]	Loss: 1.772625, lr: 0.00865 lambd: 0.10626
Train Epoch: 					1 [25600/60000 (43%)]	Loss: 1.464476, lr: 0.00766 lambd: 0.21015
Train Epoch: 					1 [38400/60000 (64%)]	Loss: 1.408526, lr: 0.00690 lambd: 0.30951
Train Epoch: 					1 [51200/60000 (85%)]	Loss: 1.244983, lr: 0.00630 lambd: 0.40253

Target Domain Test set: Average loss: 1.8369, Accuracy: 3699/10000 (37%)
Source Domain Test set: Average loss: 0.9486, Accuracy: 5973/10000 (60%)
Domains predictor:  Accuracy: 14924/20000 (75%)

Train Epoch: 					2 [0/60000 (0%)]	Loss: 1.016919, lr: 0.00595 lambd: 0.46212
Train Epoch: 					2 [12800/60000 (21%)]	Loss: 1.024209, lr: 0.00551 lambd: 0.54178
Train Epoch: 					2 [25600/60000 (43%)]	Loss: 0.965942, lr: 0.00514 lambd: 0.61276
Train Epoch: 					2 [38400/60000 (64%)]	Loss: 0.876370, lr: 0.00483 lambd: 0.67507
Train Epoch: 					2 [51200/60000 (85%)]	Loss: 1.064144, lr: 0.00455

In [0]:
def get_input_mtx(loader, model, c_size):
  X = np.zeros(c_size).T
  for batch_idx, (data, labels) in enumerate(loader):
    data = data.to(device)
    idx = batch_idx * loader.batch_size
    X[idx:idx+loader.batch_size] = model(data).cpu().detach().numpy()
  return X.T

In [0]:
def plot_digits(X, labels):
  data = []
  for i in range(len(set(labels))):
    _X = X[:, labels==i]
    [x, y, z] = _X
    trace = go.Scatter3d(x=x,y=y,z=z, name='{}'.format(i), mode = 'markers',marker = dict(
        size = 10,color = i,line = dict(width = 2,color = i, colorscale='Viridis')))
    data.append(trace)
    
  layout = dict(title = 'Styled Scatter',
                yaxis = dict(zeroline = False),
                xaxis = dict(zeroline = False)
               )

  fig = dict(data=data, layout=layout)
  plotly_plots.configure_plotly_browser_state()

  init_notebook_mode(connected=False)

  fig['layout'].update(height=800, width=1200, title='SVHN')
  plotly.offline.iplot(fig, filename='scatter')

In [0]:
X = get_input_mtx(mnist_test_loader, lambda x: model_c.get_3D(model_f(x)), (3, len(mnist_test_set)))

In [0]:
X_m = get_input_mtx(mnist_m_test_loader, lambda x: model_c.get_3D(model_f(x)), (3, len(mnist_m_test_set)))

In [0]:
X_no_relu = get_input_mtx(mnist_test_loader, lambda x: model_c.get_3D(model_f(x), activation=False), (3, len(mnist_test_set)))

In [0]:
X_labels = np.array([mnist_test_set[i][1] for i in range(len(mnist_test_set))])

In [0]:
[x,y,z] = X
trace1 = go.Scatter3d(x=x,y=y,z=z, mode='markers', marker=dict(
        size=12,line=dict(color='rgba(217, 217, 217, 0.14)',width=0.5),opacity=0.8))

[x2, y2, z2] = X_m
trace2 = go.Scatter3d(x=x2,y=y2,z=z2,mode='markers',marker=dict(
        color='rgb(127, 127, 127)',size=12,symbol='circle',line=dict(color='rgb(204, 204, 204)',width=1),opacity=0.9))

data = [trace1, trace2]
layout = go.Layout(margin=dict(l=0,r=0,b=0,t=0))
fig = go.Figure(data=data, layout=layout)

plotly_plots.configure_plotly_browser_state()

init_notebook_mode(connected=False)

fig['layout'].update(height=800, width=1200, title='MNIST')
plotly.offline.iplot(fig, filename='basic-line')

In [0]:
plot_digits(X_m, X_labels)